In [2]:
import pandas as pd

df = pd.read_csv('viz_from_tablau.csv')
df

viz_url               segment  \
0     https://public.tableau.com/app/profile/tut.by/...       news-and-events   
1     https://public.tableau.com/app/profile/iting/v...       news-and-events   
2     https://public.tableau.com/app/profile/jesse.t...       news-and-events   
3     https://public.tableau.com/app/profile/andy.kr...      learning-tableau   
4     https://public.tableau.com/app/profile/zillow....                 other   
...                                                 ...                   ...   
3281  https://public.tableau.com/app/profile/theboei...   business-dashboards   
3282  https://public.tableau.com/app/profile/airline...  time-series-analysis   
3283  https://public.tableau.com/app/profile/kpmgaut...  time-series-analysis   
3284  https://public.tableau.com/app/profile/irena.r...  time-series-analysis   
3285  https://public.tableau.com/app/profile/agata.k...            healthcare   

                                                viz_png  \
0     https://public.tableau.com/static/images/_4/_4...   
1     https://public.tableau.com/static/images/18/18...   
2     https://public.tableau.com/static/images/Na/Na...   
3     https://public.tableau.com/static/images/Vi/Vi...   
4     https://public.tableau.com/static/images/To/To...   
...                                                 ...   
3281  https://public.tableau.com/static/images/Bo/Bo...   
3282  https://public.tableau.com/static/images/Av/Av...   
3283  https://public.tableau.com/static/images/GA/GA...   
3284  https://public.tableau.com/static/images/IR/IR...   
3285  https://public.tableau.com/static/images/Th/Th...   

                                               viz_name  \
0                                Fuel Prices in Belarus   
1              Cultural tastes by gender; class and age   
2                   Tracking Party Popularity in Canada   
3                                     Visual Vocabulary   
4                                      Where to Retire?   
...                                                 ...   
3281         Boeing Commercial Market Outlook 2018-2037   
3282               Average Domestic Airfare Time Series   
3283       KPMG Global Automotive Executive Survey 2019   
3284            Renewable Energy Statistics Time Series   
3285  The Storm in My Brain | Ending the stigma of e...   

                                        author_name  \
0                                     Vadim Shmygov   
1                                         Inga Ting   
2                                    Jesse Tahirali   
3                                      Andy Kriebel   
4                          Zillow Economic Research   
...                                             ...   
3281                             The Boeing Company   
3282                           Airlines for America   
3283  KPMG Automotive (Dieter Becker, Martin Lenke)   
3284                              IRENA Data Centre   
3285                                 Agata Krawczyk   

                                         author_profile  favorite_count  \
0         https://public.tableau.com/app/profile/tut.by            16.0   
1          https://public.tableau.com/app/profile/iting            34.0   
2     https://public.tableau.com/app/profile/jesse.t...             4.0   
3     https://public.tableau.com/app/profile/andy.kr...          8579.0   
4     https://public.tableau.com/app/profile/zillow....             7.0   
...                                                 ...             ...   
3281  https://public.tableau.com/app/profile/theboei...             NaN   
3282  https://public.tableau.com/app/profile/airline...             NaN   
3283  https://public.tableau.com/app/profile/kpmgaut...             NaN   
3284  https://public.tableau.com/app/profile/irena.r...             NaN   
3285  https://public.tableau.com/app/profile/agata.k...             NaN   

      visit_count    id   VODT  repetidos  
0      12499681.0  4363   True          1  
1      

# scraoe de posteo

In [22]:
df['viz_url']

0       https://public.tableau.com/app/profile/tut.by/...
1       https://public.tableau.com/app/profile/iting/v...
2       https://public.tableau.com/app/profile/jesse.t...
3       https://public.tableau.com/app/profile/andy.kr...
4       https://public.tableau.com/app/profile/zillow....
                              ...                        
3281    https://public.tableau.com/app/profile/theboei...
3282    https://public.tableau.com/app/profile/airline...
3283    https://public.tableau.com/app/profile/kpmgaut...
3284    https://public.tableau.com/app/profile/irena.r...
3285    https://public.tableau.com/app/profile/agata.k...
Name: viz_url, Length: 3286, dtype: object

In [4]:
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
import time

# Configurar Selenium en modo headless (sin abrir ventana)
options = Options()
options.add_argument('--headless')
options.add_argument('--disable-gpu')
options.add_argument('--no-sandbox')

# Inicializar el navegador
driver = webdriver.Chrome(options=options)

# Cargar el dashboard
url = "https://public.tableau.com/app/profile/tut.by/viz/_4100/Dashboard2"
driver.get(url)

# Esperar a que cargue algo (podés ajustar esto)
time.sleep(10)

# Buscar todos los spans y ver si alguno tiene una fecha
spans = driver.find_elements(By.TAG_NAME, "span")

for span in spans:
    texto = span.text.strip()
    if texto and any(pal in texto.lower() for pal in ["20", "202", "publicado", "creado"]):
        print("Posible fecha encontrada:", texto)

driver.quit()


Posible fecha encontrada: Published: Nov 20, 2015
Posible fecha encontrada: Updated: Oct 17, 2024


In [24]:
import pandas as pd

# Asumimos que ya tenés un DataFrame llamado df con la columna 'viz_url'
# df = pd.read_excel("tu_archivo.xlsx")  # o lo que uses

# Nos aseguramos de que no haya valores nulos o duplicados
urls_unicas = df['viz_url'].dropna().drop_duplicates()

# Creamos el nuevo DataFrame con columnas vacías
df_urls = pd.DataFrame({
    'viz_url': urls_unicas,
    'Published_date': "",
    'Updated_date': ""
})

# Guardamos el CSV nuevo — no se pisa nada
csv_path = "tableau_viz_dates.csv"
df_urls.to_csv(csv_path, index=False, sep=";")
print(f"✅ CSV inicial creado con {len(df_urls)} URLs únicas.")


✅ CSV inicial creado con 3176 URLs únicas.


In [25]:
import pandas as pd
import time
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

# -------------------------- CONFIGURACIÓN --------------------------
# Ruta donde guardaremos nuestro CSV de URLs únicas y fechas.
CSV_PATH = "tableau_viz_dates.csv"



# Parámetros que te recomiendo tener a mano:
BATCH_SIZE = 10       # Cantidad de URLs que procesamos en cada iteración
TIMEOUT = 15          # Segundos máximos a esperar por cada página (configurable)
SLEEP_BETWEEN = 15    # Segundos de 'sleep' obligatorio tras cargar cada dashboard

# --------------------------------------------------------------

def obtener_fechas_de_tableau(driver, url):
    """
    1) Intenta primero encontrar el <span> que contiene <strong>Publicadas</strong> (español).
       Si lo encuentra, separa el texto con el colon y retorna solo la fecha.
    2) Lo mismo para <strong>Actualizado</strong>.
    3) Si falla ese método (por estructura distinta), cae al fallback genérico en inglés.
    """
    try:
        driver.get(url)

        # Esperamos a que cargue el contenedor principal (puede ajustarse si no es exacto)
        WebDriverWait(driver, TIMEOUT).until(
            EC.presence_of_element_located((By.XPATH, "//*[@id='root']/div/div[2]/div"))
        )
        # Un par de segundos extra para que renderice bien el contenido
        time.sleep(5)

        published = "Null"
        updated = "Null"

        # ----- Intento 1: buscar en español usando <strong> -----
        try:
            # XPath para el <span> que contiene <strong>Publicadas
            span_pub = driver.find_element(
                By.XPATH,
                "//span[strong[contains(normalize-space(text()), 'Publicad')]]"
            )
            texto_pub = span_pub.text.strip()  # Ej: "Publicadas: 3 abr 2018"
            if ":" in texto_pub:
                published = texto_pub.split(":", 1)[1].strip()
            else:
                # Si por algún motivo no hay ":", devolvemos todo
                published = texto_pub

        except Exception:
            # Si no lo encuentra en español, no hacemos nada y lo dejamos en "Null"
            pass

        try:
            # XPath para el <span> que contiene <strong>Actualizado
            span_upd = driver.find_element(
                By.XPATH,
                "//span[strong[contains(normalize-space(text()), 'Actualizado')]]"
            )
            texto_upd = span_upd.text.strip()  # Ej: "Actualizado: 19 nov 2022"
            if ":" in texto_upd:
                updated = texto_upd.split(":", 1)[1].strip()
            else:
                updated = texto_upd

        except Exception:
            # Si no lo encuentra en español, dejamos "Null"
            pass

        # Si al menos uno lo encontró en español, devolvemos esos valores
        if published != "Null" or updated != "Null":
            return published, updated

        # ----- Intento 2 (fallback en inglés): buscador genérico de "Published" / "Updated" -----
        spans = driver.find_elements(By.TAG_NAME, "span")
        for span in spans:
            texto = span.text.strip()
            if not texto:
                continue
            low = texto.lower()
            # Si viene “Published: Mar 3, 2018” u “Published Mar 3, 2018”
            if ("published:" in low or ("published" in low and any(char.isdigit() for char in texto))):
                published = texto.replace("Published:", "").strip()
            # Si viene “Updated: Oct 17, 2024” u “Updated Oct 17, 2024”
            if ("updated:" in low or ("updated" in low and any(char.isdigit() for char in texto))):
                updated = texto.replace("Updated:", "").strip()
            if published != "Null" and updated != "Null":
                break

        return published, updated

    except Exception as e:
        # Si algo falla, devolvemos (“Null”, “Null”) para no trabarnos
        print(f"[!] Error al procesar {url}: {e}")
        return "Null", "Null"


def procesar_lote(csv_path, batch_size=BATCH_SIZE):
    """
    Lee el CSV, toma los primeros batch_size registros que no tengan fechas,
    les hace scrape con Selenium, actualiza las columnas y guarda el CSV de vuelta.
    Devuelve True si procesó alguna URL, False si ya no queda nada por procesar.
    """
    df = pd.read_csv(csv_path, sep=";")
    # Filtramos filas que tengan Published_date o Updated_date vacíos o nulos.
    mask_necesitan = df["Published_date"].isnull() | df["Published_date"].astype(str).str.strip().eq("") \
                     | df["Updated_date"].isnull() | df["Updated_date"].astype(str).str.strip().eq("")
    filas_pendientes = df[mask_necesitan]

    if filas_pendientes.empty:
        print("No quedan más URLs pendientes. ¡Terminamos!")
        return False

    # Tomamos un lote de las primeras batch_size URLs pendientes
    indices_a_procesar = filas_pendientes.index[:batch_size]

    # Inicializamos Selenium (modo headless)
    options = Options()
    options.add_argument("--headless")
    options.add_argument("--disable-gpu")
    options.add_argument("--no-sandbox")
    driver = webdriver.Chrome(options=options)

    for idx in indices_a_procesar:
        url = df.at[idx, "viz_url"]
        print(f"\n→ Procesando URL (fila {idx}): {url}")
        published_date, updated_date = obtener_fechas_de_tableau(driver, url)
        df.at[idx, "Published_date"] = published_date
        df.at[idx, "Updated_date"] = updated_date
        print(f"   ⇒ Published_date: {published_date} | Updated_date: {updated_date}")

        # Guardamos inmediatamente tras cada URL procesada, para no perder nada
        df.to_csv(csv_path, index=False, sep=";")
        print("   → CSV actualizado (guardado).")

    driver.quit()
    return True


if __name__ == "__main__":
    """
    Lógica principal: repetimos procesar lotes hasta que no queden filas pendientes.
    """
    print("=== Iniciando scraping en lotes de URLs de Tableau ===")
    while True:
        hizo_algo = procesar_lote(CSV_PATH, batch_size=BATCH_SIZE)
        if not hizo_algo:
            break
        # Si quieres un "descanzo" extra entre lotes, podrías poner un sleep aquí:
        # time.sleep(5)

    print("=== Scraping completo. Todas las fechas están llenas o marcadas como 'Null'. ===")


=== Iniciando scraping en lotes de URLs de Tableau ===

→ Procesando URL (fila 0): https://public.tableau.com/app/profile/tut.by/viz/_4100/Dashboard2


C:\Users\ltf-g\AppData\Local\Temp\ipykernel_20180\1793584900.py:134: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'Nov 20, 2015' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "Published_date"] = published_date
C:\Users\ltf-g\AppData\Local\Temp\ipykernel_20180\1793584900.py:135: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'Oct 17, 2024' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "Updated_date"] = updated_date


   ⇒ Published_date: Nov 20, 2015 | Updated_date: Oct 17, 2024
   → CSV actualizado (guardado).

→ Procesando URL (fila 1): https://public.tableau.com/app/profile/iting/viz/180315_class-culture_dotplots/lit-genre
   ⇒ Published_date: 3 abr 2018 | Updated_date: 19 nov 2022
   → CSV actualizado (guardado).

→ Procesando URL (fila 2): https://public.tableau.com/app/profile/jesse.tahirali/viz/NanosNational/NATIONAL
   ⇒ Published_date: 4 sept 2015 | Updated_date: 8 mar 2023
   → CSV actualizado (guardado).

→ Procesando URL (fila 3): https://public.tableau.com/app/profile/andy.kriebel/viz/VisualVocabulary/VisualVocabulary
   ⇒ Published_date: 17 jul 2018 | Updated_date: 17 oct 2024
   → CSV actualizado (guardado).

→ Procesando URL (fila 4): https://public.tableau.com/app/profile/zillow.real.estate.research/viz/TopPlacestoRetire/Dashboard1
   ⇒ Published_date: 5 dic 2014 | Updated_date: 15 feb 2023
   → CSV actualizado (guardado).

→ Procesando URL (fila 5): https://public.tableau.com/app/

# scrape de usuarios

In [3]:
df['author_profile']

0           https://public.tableau.com/app/profile/tut.by
1            https://public.tableau.com/app/profile/iting
2       https://public.tableau.com/app/profile/jesse.t...
3       https://public.tableau.com/app/profile/andy.kr...
4       https://public.tableau.com/app/profile/zillow....
                              ...                        
3281    https://public.tableau.com/app/profile/theboei...
3282    https://public.tableau.com/app/profile/airline...
3283    https://public.tableau.com/app/profile/kpmgaut...
3284    https://public.tableau.com/app/profile/irena.r...
3285    https://public.tableau.com/app/profile/agata.k...
Name: author_profile, Length: 3286, dtype: object

In [4]:

# Paso 1: eliminamos nulos y duplicados de la columna 'author_profile'
author_urls_unicas = df['author_profile'].dropna().drop_duplicates()

# Paso 2: armamos el DataFrame con columnas vacías
df_authors = pd.DataFrame({
    'author_profile': author_urls_unicas,
    'name': "",
    'profile_png': "",
    'description': "",
    'location': "",
    'viz_count': "",
    'following': "",
    'followers': ""
})

# Paso 3: guardamos como CSV
csv_path_authors = "tableau_authors.csv"
df_authors.to_csv(csv_path_authors, index=False, sep=";")
print(f"✅ CSV de autores creado con {len(df_authors)} perfiles únicos.")

✅ CSV de autores creado con 1389 perfiles únicos.


In [7]:
import pandas as pd
import time
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

# -------------------------- CONFIGURACIÓN --------------------------
CSV_PATH = "tableau_authors.csv"  # <-- Aquí leemos y sobreescribimos el CSV de autores
BATCH_SIZE = 10       # Cuántos perfiles procesamos en cada iteración
TIMEOUT = 15          # Segundos máximos a esperar por la carga de cada página
SLEEP_BETWEEN = 5     # Segundos extra de espera tras cargar el perfil
DEBUG_MODE = False     # CAMBIA A False PARA PROCESAR TODOS LOS PERFILES
# --------------------------------------------------------------

# Selectores mejorados con más especificidad para description/location
SELECTORS = {
    "name": [
        "//h1//span[1]",
        "//h1",
        "//*[contains(@class, 'name')]//span",
        "//*[contains(@data-testid, 'name')]",
    ],
    "profile_png": [
        "//img[@data-testid='Avatar-img']",
        "//img[contains(@class, '_avatarImg_')]",
        "//img[contains(@alt, 'avatar')]",
        "//img[contains(@class, 'avatar')]",
    ],
    "desc_loc": [
        # Selectores más generales que funcionan mejor
        "//div[contains(@class, 'profile')]//p",
        "//p[contains(text(), '|') or not(contains(text(), '|'))]",
        "//*[contains(@class, 'bio')]",
        # Selectores específicos como respaldo
        "/html/body/div[2]/div/div[2]/div/div[2]/div[3]/div/p",
        "//div[contains(@class, 'profile')]//div[3]//div//p",
        "//*[contains(@class, 'description')]", 
        "//p[contains(@class, 'bio')]",
        "//div[@data-testid='profile-bio']",
    ],
    "viz_count": [
        "//a[contains(@href, 'vizzes')]//span[last()]",
        "//*[contains(@data-testid, 'viz')]//span[last()]",
        "//span[contains(text(), 'Viz')]/..//span[last()]",
        "//a[position()=1]//span[2]",
    ],
    "following": [
        "//a[contains(@href, 'following')]//span[last()]",
        "//*[contains(@data-testid, 'following')]//span[last()]",
        "//span[contains(text(), 'Following')]/..//span[last()]",
        "//a[position()=3]//span[2]",
    ],
    "followers": [
        "//a[contains(@href, 'followers')]//span[last()]",
        "//*[contains(@data-testid, 'followers')]//span[last()]",
        "//span[contains(text(), 'Followers')]/..//span[last()]",
        "//a[position()=4]//span[2]",
    ],
}


def manejar_cookies(driver):
    """
    Intenta aceptar/rechazar cookies si aparece la ventana.
    """
    time.sleep(2)  # Espera a que aparezca la ventana de cookies
    
    # Posibles selectores para botones de cookies
    cookie_selectors = [
        "//button[contains(text(), 'Accept')]",
        "//button[contains(text(), 'Aceptar')]",
        "//button[contains(text(), 'OK')]",
        "//button[contains(text(), 'Accept All')]",
        "//button[contains(text(), 'Aceptar todo')]",
        "//button[@id='onetrust-accept-btn-handler']",
        "//button[contains(@class, 'accept')]",
        "//button[contains(@class, 'cookie')]",
        "//*[@id='cookie-accept']",
        "//*[@id='accept-cookies']",
        "//div[contains(@class, 'cookie')]//button",
    ]
    
    for selector in cookie_selectors:
        try:
            cookie_btn = WebDriverWait(driver, 3).until(
                EC.element_to_be_clickable((By.XPATH, selector))
            )
            cookie_btn.click()
            print("   → Cookies aceptadas.")
            time.sleep(2)
            return True
        except:
            continue
    
    print("   → No se encontró ventana de cookies o ya fue manejada.")
    return False


def extraer_description_location(texto_completo):
    """
    Función mejorada para separar description y location basada en el patrón identificado.
    
    Reglas:
    1. Si hay "|", dividir por el ÚLTIMO "|"
    2. Todo antes del último "|" = description
    3. Todo después del último "|" = location (limpiando espacios)
    4. Si no hay "|", todo es description y location = "Null"
    
    Ejemplos:
    - "🎨 Sr. BI-developer, Tableau Consultant en Volkswagen Digital Solutions | Lisbon, Portugal"
      → description: "🎨 Sr. BI-developer, Tableau Consultant en Volkswagen Digital Solutions"
      → location: "Lisbon, Portugal"
    
    - "ABC News | Sydney, Australia"
      → description: "ABC News"
      → location: "Sydney, Australia"
    
    - "McKinsey & Company"
      → description: "McKinsey & Company"
      → location: "Null"
    """
    if not texto_completo or texto_completo == "Null":
        return "Null", "Null"
    
    texto_completo = texto_completo.strip()
    
    if "|" in texto_completo:
        # Dividir por el ÚLTIMO "|"
        last_pipe_index = texto_completo.rfind("|")
        description = texto_completo[:last_pipe_index].strip()
        location = texto_completo[last_pipe_index + 1:].strip()
        
        # Si alguna parte queda vacía, asignar "Null"
        if not description:
            description = "Null"
        if not location:
            location = "Null"
            
        return description, location
    else:
        # No hay "|", todo es description
        return texto_completo, "Null"


def obtener_datos_autor(driver, url):
    """
    Abre el perfil de autor y extrae:
      - name
      - profile_png (src del <img>)
      - description | location (separados por "|")
      - viz_count
      - following
      - followers

    Si no encuentra algo, deja 'Null'.
    """
    print(f"   → Navegando a: {url}")
    driver.get(url)
    
    # Manejar cookies primero
    manejar_cookies(driver)

    # Esperamos a que aparezca cualquier elemento del perfil
    elemento_encontrado = False
    for selector in SELECTORS["name"]:
        try:
            WebDriverWait(driver, TIMEOUT).until(
                EC.presence_of_element_located((By.XPATH, selector))
            )
            print("   → Página cargada correctamente.")
            elemento_encontrado = True
            break
        except:
            continue
    
    if not elemento_encontrado:
        print("   → No se pudo cargar la página o encontrar elementos.")
        # Tomamos screenshot para debug
        try:
            driver.save_screenshot(f"debug_screenshot_{int(time.time())}.png")
            print("   → Screenshot guardado para debug.")
            # También guardamos el HTML para debug
            with open(f"debug_html_{int(time.time())}.html", "w", encoding="utf-8") as f:
                f.write(driver.page_source)
            print("   → HTML guardado para debug.")
        except:
            pass
        
        return {
            "name": "Null",
            "profile_png": "Null",
            "description": "Null",
            "location": "Null",
            "viz_count": "Null",
            "following": "Null",
            "followers": "Null",
        }

    # Damos un pequeño respiro extra para que termine de cargar todo
    time.sleep(SLEEP_BETWEEN)

    def obtener_texto_flexible(campo):
        """Intenta obtener texto con múltiples selectores"""
        for selector in SELECTORS[campo]:
            try:
                elemento = driver.find_element(By.XPATH, selector)
                texto = elemento.text.strip()
                if texto:  # Solo devolvemos si encontramos texto
                    print(f"   → Selector exitoso para {campo}: {selector}")
                    return texto
            except Exception as e:
                print(f"   → Selector fallido para {campo}: {selector} - {str(e)}")
                continue
        return "Null"

    def obtener_src_flexible(campo):
        """Intenta obtener src con múltiples selectores"""
        for selector in SELECTORS[campo]:
            try:
                elemento = driver.find_element(By.XPATH, selector)
                src = elemento.get_attribute("src")
                if src and src.strip():  # Solo devolvemos si encontramos src
                    print(f"   → Selector exitoso para {campo}: {selector}")
                    return src.strip()
            except Exception as e:
                if DEBUG_MODE:  # Solo mostrar errores en modo debug
                    print(f"   → Selector fallido para {campo}: {selector} - {str(e)}")
                continue
        return "Null"

    # Extraemos cada campo con logging detallado
    print("   → Extrayendo datos del perfil...")
    
    name = obtener_texto_flexible("name")
    print(f"   → name encontrado: {name}")
    
    profile_png = obtener_src_flexible("profile_png")
    print(f"   → profile_png encontrado: {profile_png}")
    
    desc_loc_full = obtener_texto_flexible("desc_loc")
    print(f"   → desc_loc_full encontrado: '{desc_loc_full}'")
    
    # MEJORA PRINCIPAL: Usar la función especializada para separar description y location
    description, location = extraer_description_location(desc_loc_full)
    print(f"   → description procesada: '{description}'")
    print(f"   → location procesada: '{location}'")
    
    viz_count = obtener_texto_flexible("viz_count")
    print(f"   → viz_count encontrado: {viz_count}")
    
    following = obtener_texto_flexible("following")
    print(f"   → following encontrado: {following}")
    
    followers = obtener_texto_flexible("followers")
    print(f"   → followers encontrado: {followers}")

    return {
        "name": name,
        "profile_png": profile_png,
        "description": description,
        "location": location,
        "viz_count": viz_count,
        "following": following,
        "followers": followers,
    }


def procesar_lote_autores(csv_path, batch_size=BATCH_SIZE):
    """
    1) Lee 'tableau_authors.csv'.
    2) Filtra perfiles que aún no tengan 'name' (o cualquiera vacío).
    3) Toma los primeros batch_size índices pendientes.
    4) Por cada uno: hace scrape y actualiza filas en el DataFrame.
    5) Guarda el CSV inmediatamente tras cada perfil procesado.
    6) Retorna True si procesó al menos uno, False si ya no quedan pendientes.
    """
    df = pd.read_csv(csv_path, sep=";")

    # Filtramos filas donde al menos 'name' esté vacío o 'Null'
    mask_pendientes = (
        df["name"].isnull()
        | df["name"].astype(str).str.strip().eq("")
        | df["name"].astype(str).eq("Null")
    )
    pendientes = df[mask_pendientes]

    if pendientes.empty:
        print("No quedan perfiles de autor pendientes. ¡Todo listo!")
        return False

    # En modo DEBUG, solo procesamos el primer enlace
    if DEBUG_MODE:
        indices = [pendientes.index[0]]
        print(f"🐛 MODO DEBUG: Procesando solo el primer enlace (fila {indices[0]})")
    else:
        indices = pendientes.index[:batch_size]

    # Inicializamos Selenium - SIEMPRE headless
    options = Options()
    options.add_argument("--headless")  # SIEMPRE sin ventana
    options.add_argument("--disable-gpu")
    options.add_argument("--no-sandbox")
    options.add_argument("--disable-dev-shm-usage")
    options.add_argument("--window-size=1920,1080")
    # Agregar user-agent para evitar detección de bot
    options.add_argument("--user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36")
    # Opciones adicionales para mejor rendimiento
    options.add_argument("--disable-extensions")
    options.add_argument("--disable-plugins")
    options.add_argument("--disable-images")
    
    driver = webdriver.Chrome(options=options)

    for idx in indices:
        url = df.at[idx, "author_profile"]
        print(f"\n→ Procesando autor (fila {idx}): {url}")

        try:
            datos = obtener_datos_autor(driver, url)
        except Exception as e:
            print(f"[!] Error scrapeando {url}. Marcamos todo 'Null'. — {e}")
            datos = {
                "name": "Null",
                "profile_png": "Null",
                "description": "Null",
                "location": "Null",
                "viz_count": "Null",
                "following": "Null",
                "followers": "Null",
            }

        # Actualizamos el DataFrame con los valores obtenidos (o 'Null')
        # Convertimos a string para evitar warnings de pandas
        df.at[idx, "name"] = str(datos["name"])
        df.at[idx, "profile_png"] = str(datos["profile_png"])
        df.at[idx, "description"] = str(datos["description"])
        df.at[idx, "location"] = str(datos["location"])
        df.at[idx, "viz_count"] = str(datos["viz_count"])
        df.at[idx, "following"] = str(datos["following"])
        df.at[idx, "followers"] = str(datos["followers"])

        print(f"   ⇒ name: {datos['name']}")
        print(f"   ⇒ profile_png: {datos['profile_png']}")
        print(f"   ⇒ description: {datos['description']}")
        print(f"   ⇒ location: {datos['location']}")
        print(f"   ⇒ viz_count: {datos['viz_count']}")
        print(f"   ⇒ following: {datos['following']}")
        print(f"   ⇒ followers: {datos['followers']}")

        # Guardamos el CSV tras cada perfil
        df.to_csv(csv_path, index=False, sep=";")
        print("   → CSV de autores actualizado (guardado).")
        
        # En modo debug, solo procesamos uno
        if DEBUG_MODE:
            break

    driver.quit()
    return True


# Función principal para ejecutar en Jupyter
def ejecutar_scraping():
    """
    Función principal para ejecutar desde Jupyter Notebook
    """
    if DEBUG_MODE:
        print("🐛 === MODO DEBUG: Scraping del primer enlace solamente ===")
    else:
        print("=== Iniciando scraping en lotes para 'tableau_authors.csv' ===")
        
    while True:
        hizo_algo = procesar_lote_autores(CSV_PATH, batch_size=BATCH_SIZE)
        if not hizo_algo:
            break
        # En modo debug, solo hacemos una iteración
        if DEBUG_MODE:
            break
        # Podrías pausar un par de segundos aquí si el servidor se enfada:
        # time.sleep(2)
    
    if DEBUG_MODE:
        print("🐛 === Debug completado. Revisa los resultados y cambia DEBUG_MODE=False para procesar todos ===")
    else:
        print("=== Scraping de autores completado. ===")


# Función de prueba para validar la lógica de separación
def test_extraction():
    """
    Función para probar la lógica de extracción con tus ejemplos
    """
    test_cases = [
        "🎨 Sr. BI-developer, Tableau Consultant en Volkswagen Digital Solutions | Lisbon, Portugal",
        "ABC News | Sydney, Australia", 
        "Founder & Creator en Next-Level Tableau | London, United Kingdom",
        "McKinsey & Company",
        "Executive Director of Visual Analytics en Clemson University | Clemson, South Carolina, United States"
    ]
    
    print("=== PRUEBA DE EXTRACCIÓN ===")
    for i, test_text in enumerate(test_cases, 1):
        description, location = extraer_description_location(test_text)
        print(f"\nEjemplo {i}:")
        print(f"Texto original: '{test_text}'")
        print(f"Description: '{description}'")
        print(f"Location: '{location}'")
    print("=== FIN PRUEBA ===")


if __name__ == "__main__":
    """
    Bucle principal: repetimos procesar lotes hasta que no queden filas pendientes.
    """
    # Uncomment to test extraction logic
    # test_extraction()
    
    if DEBUG_MODE:
        print("🐛 === MODO DEBUG: Scraping del primer enlace solamente ===")
    else:
        print("=== Iniciando scraping en lotes para 'tableau_authors.csv' ===")
        
    while True:
        hizo_algo = procesar_lote_autores(CSV_PATH, batch_size=BATCH_SIZE)
        if not hizo_algo:
            break
        # En modo debug, solo hacemos una iteración
        if DEBUG_MODE:
            break
        # Podrías pausar un par de segundos aquí si el servidor se enfada:
        # time.sleep(2)
    
    if DEBUG_MODE:
        print("🐛 === Debug completado. Revisa los resultados y cambia DEBUG_MODE=False para procesar todos ===")
    else:
        print("=== Scraping de autores completado. ===")

=== Iniciando scraping en lotes para 'tableau_authors.csv' ===

→ Procesando autor (fila 2): https://public.tableau.com/app/profile/jesse.tahirali
   → Navegando a: https://public.tableau.com/app/profile/jesse.tahirali
   → Cookies aceptadas.
   → Página cargada correctamente.
   → Extrayendo datos del perfil...
   → Selector exitoso para name: //h1//span[1]
   → name encontrado: Jesse Tahirali
   → Selector exitoso para profile_png: //img[@data-testid='Avatar-img']
   → profile_png encontrado: https://public.tableau.com/app/assets/defaultAvatar-BZdDTul6.png
   → Selector fallido para desc_loc: //div[contains(@class, 'profile')]//p - Message: no such element: Unable to locate element: {"method":"xpath","selector":"//div[contains(@class, 'profile')]//p"}
  (Session info: chrome=136.0.7103.93); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#no-such-element-exception
Stacktrace:
	GetHandleVerifier [0x00007FF64318CF45+

C:\Users\ltf-g\AppData\Local\Temp\ipykernel_24480\3217322786.py:340: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '7' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "viz_count"] = str(datos["viz_count"])
C:\Users\ltf-g\AppData\Local\Temp\ipykernel_24480\3217322786.py:341: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "following"] = str(datos["following"])
C:\Users\ltf-g\AppData\Local\Temp\ipykernel_24480\3217322786.py:342: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '7' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "followers"] = str(datos["followers"])


   → No se encontró ventana de cookies o ya fue manejada.
   → Página cargada correctamente.
   → Extrayendo datos del perfil...
   → Selector exitoso para name: //h1//span[1]
   → name encontrado: Andy Kriebel
   → Selector exitoso para profile_png: //img[@data-testid='Avatar-img']
   → profile_png encontrado: https://public.tableau.com/avatar/9f570512-d432-4242-b0c7-d1e44b7a3e6b.jpeg
   → Selector fallido para desc_loc: //div[contains(@class, 'profile')]//p - Message: no such element: Unable to locate element: {"method":"xpath","selector":"//div[contains(@class, 'profile')]//p"}
  (Session info: chrome=136.0.7103.93); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#no-such-element-exception
Stacktrace:
	GetHandleVerifier [0x00007FF64318CF45+75717]
	GetHandleVerifier [0x00007FF64318CFA0+75808]
	(No symbol) [0x00007FF642F58F9A]
	(No symbol) [0x00007FF642FAF4C6]
	(No symbol) [0x00007FF642FAF77C]
	(No symbol) [0x00007

C:\Users\ltf-g\AppData\Local\Temp\ipykernel_24480\3217322786.py:340: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '69' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "viz_count"] = str(datos["viz_count"])
C:\Users\ltf-g\AppData\Local\Temp\ipykernel_24480\3217322786.py:341: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '63' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "following"] = str(datos["following"])
C:\Users\ltf-g\AppData\Local\Temp\ipykernel_24480\3217322786.py:342: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '203' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "followers"] = str(datos["followers"])


   → CSV de autores actualizado (guardado).

→ Procesando autor (fila 13): https://public.tableau.com/app/profile/peter.james.walker
   → Navegando a: https://public.tableau.com/app/profile/peter.james.walker
   → No se encontró ventana de cookies o ya fue manejada.
   → Página cargada correctamente.
   → Extrayendo datos del perfil...
   → Selector exitoso para name: //h1//span[1]
   → name encontrado: Peter James Walker
   → Selector exitoso para profile_png: //img[@data-testid='Avatar-img']
   → profile_png encontrado: https://public.tableau.com/avatar/ab1bb348-54cf-4fdd-8515-39ed31964b90.jpeg
   → Selector fallido para desc_loc: //div[contains(@class, 'profile')]//p - Message: no such element: Unable to locate element: {"method":"xpath","selector":"//div[contains(@class, 'profile')]//p"}
  (Session info: chrome=136.0.7103.93); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#no-such-element-exception
Stacktrace:


...

   → No se encontró ventana de cookies o ya fue manejada.
   → Página cargada correctamente.
   → Extrayendo datos del perfil...
   → Selector exitoso para name: //h1//span[1]
   → name encontrado: Dave Hart
   → Selector exitoso para profile_png: //img[@data-testid='Avatar-img']
   → profile_png encontrado: https://public.tableau.com/app/assets/defaultAvatar-BZdDTul6.png
   → Selector fallido para desc_loc: //div[contains(@class, 'profile')]//p - Message: no such element: Unable to locate element: {"method":"xpath","selector":"//div[contains(@class, 'profile')]//p"}
  (Session info: chrome=136.0.7103.93); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#no-such-element-exception
Stacktrace:
	GetHandleVerifier [0x00007FF64318CF45+75717]
	GetHandleVerifier [0x00007FF64318CFA0+75808]
	(No symbol) [0x00007FF642F58F9A]
	(No symbol) [0x00007FF642FAF4C6]
	(No symbol) [0x00007FF642FAF77C]
	(No symbol) [0x00007FF643002577]
	

C:\Users\ltf-g\AppData\Local\Temp\ipykernel_24480\3217322786.py:340: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '4' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "viz_count"] = str(datos["viz_count"])


   → No se encontró ventana de cookies o ya fue manejada.
   → Página cargada correctamente.
   → Extrayendo datos del perfil...
   → Selector exitoso para name: //h1//span[1]
   → name encontrado: Bradley Woodrum
   → Selector exitoso para profile_png: //img[@data-testid='Avatar-img']
   → profile_png encontrado: https://public.tableau.com/avatar/55fa2d0e-bbf3-4478-8dd3-6f1695de894a.jpeg
   → Selector fallido para desc_loc: //div[contains(@class, 'profile')]//p - Message: no such element: Unable to locate element: {"method":"xpath","selector":"//div[contains(@class, 'profile')]//p"}
  (Session info: chrome=136.0.7103.93); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#no-such-element-exception
Stacktrace:
	GetHandleVerifier [0x00007FF64318CF45+75717]
	GetHandleVerifier [0x00007FF64318CFA0+75808]
	(No symbol) [0x00007FF642F58F9A]
	(No symbol) [0x00007FF642FAF4C6]
	(No symbol) [0x00007FF642FAF77C]
	(No symbol) [0x00

C:\Users\ltf-g\AppData\Local\Temp\ipykernel_24480\3217322786.py:340: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '2' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[idx, "viz_count"] = str(datos["viz_count"])


   → No se encontró ventana de cookies o ya fue manejada.
   → Página cargada correctamente.
   → Extrayendo datos del perfil...
   → Selector exitoso para name: //h1//span[1]
   → name encontrado: ZON
   → Selector exitoso para profile_png: //img[@data-testid='Avatar-img']
   → profile_png encontrado: https://public.tableau.com/app/assets/defaultAvatar-BZdDTul6.png
   → Selector fallido para desc_loc: //div[contains(@class, 'profile')]//p - Message: no such element: Unable to locate element: {"method":"xpath","selector":"//div[contains(@class, 'profile')]//p"}
  (Session info: chrome=136.0.7103.93); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#no-such-element-exception
Stacktrace:
	GetHandleVerifier [0x00007FF64318CF45+75717]
	GetHandleVerifier [0x00007FF64318CFA0+75808]
	(No symbol) [0x00007FF642F58F9A]
	(No symbol) [0x00007FF642FAF4C6]
	(No symbol) [0x00007FF642FAF77C]
	(No symbol) [0x00007FF643002577]
	(No sy

# Scrape de png

In [14]:
df['viz_png'].head(10)

0    https://public.tableau.com/static/images/_4/_4...
1    https://public.tableau.com/static/images/18/18...
2    https://public.tableau.com/static/images/Na/Na...
3    https://public.tableau.com/static/images/Vi/Vi...
4    https://public.tableau.com/static/images/To/To...
5    https://public.tableau.com/static/images/Ge/Ge...
6    https://public.tableau.com/static/images/Ar/Ar...
7    https://public.tableau.com/static/images/hs/hs...
8    https://public.tableau.com/static/images/Th/Th...
9    https://public.tableau.com/static/images/Ap/Ap...
Name: viz_png, dtype: object

In [9]:
# Tomamos únicamente los valores no nulos y únicos de 'viz_url'
unique_viz_urls = df["viz_png"].dropna().drop_duplicates().reset_index(drop=True)

# Creamos el DataFrame para PNGs
df_png = pd.DataFrame({
    "viz_url": unique_viz_urls,
    "png_path": ""    # Aquí vamos a guardar luego la ruta al PNG
})

# Guardamos el CSV base (solo URLs + columna vacía)
csv_png_path = "tableau_viz_png.csv"
df_png.to_csv(csv_png_path, index=False, sep=";")
print(f"✅ CSV base '{csv_png_path}' creado con {len(df_png)} URLs únicas.")

✅ CSV base 'tableau_viz_png.csv' creado con 3176 URLs únicas.


In [10]:
import os
import pandas as pd
import requests
from urllib.parse import urlparse

def cargar_csv_existente():
    """Carga el CSV existente tableau_viz_png.csv"""
    csv_path = "tableau_viz_png.csv"
    
    if not os.path.exists(csv_path):
        print(f"❌ Error: No se encontró el archivo {csv_path}")
        return None
    
    print(f"📄 Cargando CSV: {csv_path}")
    df = pd.read_csv(csv_path, sep=";")
    
    print(f"📊 Total de URLs: {len(df)}")
    print(f"📋 Columnas: {list(df.columns)}")
    
    return df

def encontrar_primera_pendiente(df):
    """Encuentra la primera fila sin png_path procesado"""
    mask = (
        df['png_path'].isna() | 
        (df['png_path'] == '') | 
        (df['png_path'].astype(str).str.strip() == '') |
        (df['png_path'].astype(str).str.strip() == 'nan')
    )
    
    pendientes = df[mask]
    
    print(f"📋 URLs pendientes: {len(pendientes)}")
    
    if len(pendientes) == 0:
        print("✅ No hay URLs pendientes")
        return None, None
    
    # Tomar la primera pendiente
    idx = pendientes.index[0]
    url = df.loc[idx, 'viz_url']
    
    print(f"→ Procesando fila {idx}")
    print(f"   URL: {url}")
    return idx, url

def descargar_png_directo(url, output_path):
    """Descarga PNG directamente desde la URL"""
    try:
        print(f"🌐 Descargando: {url}")
        
        # Headers para simular un navegador
        headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36'
        }
        
        # Descargar la imagen
        response = requests.get(url, headers=headers, timeout=30)
        response.raise_for_status()  # Lanza excepción si hay error HTTP
        
        # Verificar que es una imagen PNG
        content_type = response.headers.get('content-type', '')
        if 'image' not in content_type.lower():
            print(f"⚠️ Advertencia: Content-Type no es imagen: {content_type}")
        
        # Guardar el archivo
        with open(output_path, 'wb') as f:
            f.write(response.content)
        
        # Verificar que se guardó correctamente
        if os.path.exists(output_path):
            size = os.path.getsize(output_path)
            print(f"✅ PNG descargado: {size} bytes -> {output_path}")
            return True
        else:
            print("❌ Error: El archivo no se creó")
            return False
            
    except requests.exceptions.RequestException as e:
        print(f"❌ Error de descarga: {e}")
        return False
    except Exception as e:
        print(f"❌ Error inesperado: {e}")
        return False

def generar_nombre_archivo(idx, url):
    """Genera nombre de archivo basado en el índice y URL"""
    # Extraer parte del nombre de la URL para hacerlo más descriptivo
    parsed = urlparse(url)
    path_parts = parsed.path.split('/')
    
    # Buscar partes útiles del path
    name_parts = [part for part in path_parts if part and part != 'static' and part != 'images']
    
    if name_parts:
        # Usar las primeras partes como nombre base
        base_name = "_".join(name_parts[:2])  # Tomar máximo 2 partes
        # Limpiar caracteres problemáticos
        base_name = "".join(c for c in base_name if c.isalnum() or c in "_-")
        filename = f"viz_{idx}_{base_name}.png"
    else:
        filename = f"viz_{idx}.png"
    
    return filename

def main():
    print("🚀 DESCARGADOR DIRECTO DE PNGs DE TABLEAU")
    print("=" * 50)
    
    # 1. Cargar CSV existente
    df = cargar_csv_existente()
    if df is None:
        return
    
    # 2. Encontrar primera URL pendiente
    idx, url = encontrar_primera_pendiente(df)
    if idx is None:
        return
    
    # 3. Preparar carpeta de salida
    output_folder = "viz_png"
    os.makedirs(output_folder, exist_ok=True)
    
    # 4. Generar nombre de archivo
    png_filename = generar_nombre_archivo(idx, url)
    png_path = os.path.join(output_folder, png_filename)
    
    print(f"📁 Archivo de salida: {png_path}")
    
    # 5. Descargar PNG directamente
    exito = descargar_png_directo(url, png_path)
    
    if exito:
        # 6. Actualizar CSV
        df.loc[idx, 'png_path'] = png_path
        df.to_csv("tableau_viz_png.csv", index=False, sep=";")
        print(f"✅ CSV actualizado - fila {idx} completada")
        
        # 💤 Aquí viene la siestita entre descargas
        tiempo_espera = random.uniform(0.5, 1.5)
        print(f"⏳ Esperando {tiempo_espera:.2f} segundos antes de continuar...")
        time.sleep(tiempo_espera)
        
    else:
        print("❌ No se pudo descargar la imagen")
    
    print("=" * 50)
    print("🏁 DESCARGA TERMINADA")

# Ejecutar directamente (sin if __name__)
main()

🚀 DESCARGADOR DIRECTO DE PNGs DE TABLEAU
📄 Cargando CSV: tableau_viz_png.csv
📊 Total de URLs: 3176
📋 Columnas: ['viz_url', 'png_path']
📋 URLs pendientes: 3176
→ Procesando fila 0
   URL: https://public.tableau.com/static/images/_4/_4100/Dashboard2/4_3.png
📁 Archivo de salida: viz_png\viz_0__4__4100.png
🌐 Descargando: https://public.tableau.com/static/images/_4/_4100/Dashboard2/4_3.png
✅ PNG descargado: 104510 bytes -> viz_png\viz_0__4__4100.png
✅ CSV actualizado - fila 0 completada
⏳ Esperando 1.40 segundos antes de continuar...


C:\Users\ltf-g\AppData\Local\Temp\ipykernel_24480\1575575794.py:135: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'viz_png\viz_0__4__4100.png' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.loc[idx, 'png_path'] = png_path


🏁 DESCARGA TERMINADA


#### continuar en bucle

In [11]:
import time
import random

def main():
    print("🚀 DESCARGADOR DIRECTO DE PNGs DE TABLEAU")
    print("=" * 50)

    # 1. Cargar CSV existente
    df = cargar_csv_existente()
    if df is None:
        return

    # 2. Preparar carpeta de salida
    output_folder = "viz_png"
    os.makedirs(output_folder, exist_ok=True)

    # 3. Loop principal
    while True:
        idx, url = encontrar_primera_pendiente(df)
        if idx is None:
            break  # No quedan más

        # 4. Generar nombre de archivo
        png_filename = generar_nombre_archivo(idx, url)
        png_path = os.path.join(output_folder, png_filename)

        print(f"📁 Archivo de salida: {png_path}")

        # 5. Descargar PNG
        exito = descargar_png_directo(url, png_path)

        if exito:
            # 6. Actualizar CSV
            df.loc[idx, 'png_path'] = png_path
            df.to_csv("tableau_viz_png.csv", index=False, sep=";")
            print(f"✅ CSV actualizado - fila {idx} completada")

            # 💤 Siestita entre descargas
            tiempo_espera = random.uniform(0.5, 1.5)
            print(f"⏳ Esperando {tiempo_espera:.2f} segundos antes de continuar...")
            time.sleep(tiempo_espera)

        else:
            print(f"❌ Falla al descargar fila {idx}. Saltando...")

    print("=" * 50)
    print("🏁 TODAS LAS DESCARGAS TERMINADAS")

# Ejecutar
main()


🚀 DESCARGADOR DIRECTO DE PNGs DE TABLEAU
📄 Cargando CSV: tableau_viz_png.csv
📊 Total de URLs: 3176
📋 Columnas: ['viz_url', 'png_path']
📋 URLs pendientes: 3175
→ Procesando fila 1
   URL: https://public.tableau.com/static/images/18/180315_class-culture_dotplots/lit-genre/4_3.png
📁 Archivo de salida: viz_png\viz_1_18_180315_class-culture_dotplots.png
🌐 Descargando: https://public.tableau.com/static/images/18/180315_class-culture_dotplots/lit-genre/4_3.png
✅ PNG descargado: 110150 bytes -> viz_png\viz_1_18_180315_class-culture_dotplots.png
✅ CSV actualizado - fila 1 completada
⏳ Esperando 1.35 segundos antes de continuar...
📋 URLs pendientes: 3174
→ Procesando fila 2
   URL: https://public.tableau.com/static/images/Na/NanosNational/NATIONAL/4_3.png
📁 Archivo de salida: viz_png\viz_2_Na_NanosNational.png
🌐 Descargando: https://public.tableau.com/static/images/Na/NanosNational/NATIONAL/4_3.png
✅ PNG descargado: 138020 bytes -> viz_png\viz_2_Na_NanosNational.png
✅ CSV actualizado - fila 2 co